## Objectif du notebook

* Download de la bdtopo pour une année donnée pour les départements de la métropole de Lyon (Ain, Isère, Rhone)
* Extraction des batiments industriels et communes dans la zone d'étude passée en entrée
* Sauvegarde locale des fichiers

Attention, les operations de joins doivent prendre en compte l'entièreté des communes intersectés par le buffer

In [3]:
import geopandas as gpd 
import pandas as pd 
import os 
import numpy as np 
import folium
from shapely import Point
from py7zr import unpack_7zarchive
from pathlib import Path
import shutil
import requests
import shutil
from bs4 import BeautifulSoup
from typing import List, Dict, Any

In [4]:
from src.config import *

In [5]:
def _download(url): 
    try:
        res = requests.get(url)
    except:
        raise HTTPError("url not valid")
    if res.status_code == 200:
        return res.content
    else:
        raise HTTPError("Download Fail")

In [6]:
def download_html(url): 
    return _download(url)
    
def download_7z(url, out_dir):
    print(f"Go to to {url}")
    content =  _download(url)
    out_path = os.path.join(out_dir, os.path.basename(url))
    with open(out_path, 'wb') as out:
        out.write(content)
    print(f"{out_path} downloaded !")
    return out_path

In [7]:
def parse_html(content, dept: str, year: int, format="SHP"):
    
    soup = BeautifulSoup(content, "html.parser")
    hrefs = [_["href"] for _ in soup.find_all('a', href=True)]
    
    code_dept = dept.zfill(3)
    pattern = f"D{code_dept}_{year}"
    
    href = [_ for _ in hrefs if (pattern in _) and (format in _) and (_.endswith(".7z"))]
    if not href: 
        raise ValueError(f"archive file not found for {dept} - {year}")
    if  len(href) > 1: 
        # select ancient update = keep old nomenclature
        tuple_href = [(Path(h).stem, h) for h in href]
        return sorted(tuple_href, key= lambda x: x[0], reverse=False)[0][1]
        
    return href[0]

In [8]:
def download_bdtopo(out_dir:str,
                    dept: str, 
                    year: int, 
                    url:str, 
                    format="SHP"):
    content = download_html(url)
    href = parse_html(content, dept, year)
    out_path = os.path.join(out_dir, os.path.basename(href))
    
    if not os.path.exists(out_path):
        out_path = download_7z(href, out_dir)
    else:
        print(f"skip download for {dept} on {year}")
    return out_path

In [9]:
def extract_7z(arch_path, out_dir): 
    
    fname = Path(arch_path).stem
    out_path = os.path.join(out_dir, fname)
    if not os.path.exists(out_path):
    
        print(f"extration process... {arch_path}")
        if not any([_[0] == "7zip" for _ in shutil.get_unpack_formats()]):
            shutil.register_unpack_format('7zip', ['.7z'], unpack_7zarchive)
        shutil.unpack_archive(arch_path, out_dir)
        print(f"extracted {os.path.join(out_dir, fname)}")
    else:
        print(f"Archive already extracted : {out_path}")
    return out_path

In [10]:
def check_dir(*path):
    os.makedirs(os.path.join(*path), exist_ok=True)
    return os.path.join(*path)

In [11]:
def extract_bati_path(dir_path):
    
    target_bati_dir = ["E_BATI", "BATI"]
    target_dir_path=None
    for r, dirs, _ in os.walk(dir_path): 
        if any([_ for _ in dirs if _ in target_bati_dir]):
            dir_name = [_ for _ in dirs if _ in target_bati_dir][0]
            target_dir_path = os.path.join(r, dir_name)
            break  
    if not target_dir_path:
        raise ValueError("please check file paths")
    return target_dir_path


def _extract_bati_new_bdtopo(list_path): 
    """
    nomenclature >=2023
    """
    
    nature = "Industriel, agricole ou commercial"
    usage = "Industriel"
    usage1b = "Commercial et services"
    print("new nomenclature")
    list_df = []
    
    gen_df = (gpd.read_file(path, crs=CRS) for path in list_path) 
    
    for df in gen_df:
        list_df.append(
            df[
            ((df["NATURE"] == nature) & (df["USAGE1"] == usage)) | 
            ((df["NATURE"] == nature) & (df["USAGE1"] == usage1b) & (df["USAGE2"] == usage))
            ]
        )
    return list_df
 

def _extract_bati_old_bdtopo(list_path): 
    list_df = [gpd.read_file(path, crs=CRS) for path in list_path]
    return list_df
    
    
def extract_bati_indus(list_path, year): 
    
    years_new_nomenclature = ["2023"]
    
    if year in years_new_nomenclature:
        return _extract_bati_new_bdtopo(list_path)
    else:
        return _extract_bati_old_bdtopo(list_path)

    

def extract_bati_on_roi(path, roi, year):

    
    target_prefix_f = ["BATI_INDUSTRIEL", "BATIMENT"]
    target_suffix_f = ".shp"
    
    target_f_path = [os.path.join(path, f) for f in os.listdir(path) if (Path(f).stem in target_prefix_f) and f.lower().endswith(target_suffix_f)]
    
    list_df = extract_bati_indus(target_f_path, year)
    
    list_df = [gpd.sjoin(df, roi, how="inner", predicate="within") for df in list_df]
    df_y = pd.concat(list_df)
    
    return df_y

def extract_communes_path(dir, ext): 
    target_dir_path = None
    for r, dirs, files in os.walk(dir): 
        if any([_ for _ in files if _ == f"COMMUNE{ext}"]):
            target_dir_path = os.path.join(r, f"COMMUNE{ext}")
            break
    return target_dir_path

def extract_communes_on_roi(path, roi):
    """
    extracts communes which intersects roi buffer
    """
    df = gpd.read_file(path, crs=CRS)
    df = gpd.sjoin(df, roi, how="inner", predicate="intersects").drop("index_right", axis=1)
    return df

In [15]:
def pipeline_bdtopo_year(data_dir:str,
                    dept_list: List[str],
                    name_roi: str,
                    year: int, 
                    url=url, 
                    centroid: tuple=centroid_lyon,
                    format="SHP", 
                    clean_dir=True):

    out_dir_raw = check_dir(data_dir, "raw", "BDTOPO", year)
    out_dir_processed = check_dir(data_dir, "processed", "BDTOPO", name_roi, year)

    ext_file = ".SHP" if year !="2023" else ".shp"

    # define roi
    roi = gpd.GeoDataFrame(geometry=[Point(centroid)], crs=CRS).buffer(DIST_RADIUS).to_frame()

    paths_bati = []
    paths_communes = []
    
    for dept in dept_list:

        # download bdtopo
        arch_path = download_bdtopo(out_dir_raw, dept, year, url, format=format)
        bd_path = extract_7z(arch_path, out_dir_raw)
        print(f"work on {bd_path}")
        # extract building on roi
        paths_bati.append(extract_bati_path(bd_path))
        # extract communes on roi
        paths_communes.append(extract_communes_path(bd_path, ext_file))

    print("-- Process buildings and communes --")

    # extract building and communes
    communes = [extract_communes_on_roi(path, roi) for path in paths_communes]
    communes = pd.concat(communes)

    # define unary_union roi based on communes
    rio_com_union = gpd.sjoin(communes, roi, how="inner", predicate="intersects").drop("index_right", axis=1).dissolve()
    
    # extract building on communes
    bati =[extract_bati_on_roi(path, rio_com_union, year) for path in paths_bati]
    bati = pd.concat(bati)


    bati.to_file(os.path.join(out_dir_processed, f"bati_indus_{name_roi}_{year}.shp"))
    communes.to_file(os.path.join(out_dir_processed, f"communes_{year}.shp"))

    print(f"year {year} done")
    if clean_dir: 
        shutil.rmtree(bd_path)
    

### Pipeline extraction

In [18]:
url = "https://geoservices.ign.fr/bdtopo"
dept_list = ["01", "38", "69"]
name_roi = "lyon"
selected_year = ["2008", "2013" ,"2023"] 
DIST_RADIUS = 25_000
centroid_lyon =  [841650.0, 6517765.0]
CRS = 2154

In [19]:
for year in selected_year:
    print(f"==== {year} ====")
    pipeline_bdtopo_year(data_dir="../data",
                        dept_list=dept_list,
                        name_roi=name_roi,
                        year=year, 
                        url=url, 
                        centroid=centroid_lyon,
                        format="SHP", 
                        clean_dir=False)

==== 2008 ====
skip download for 01 on 2008
Archive already extracted : ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D001_2008-09-14
work on ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D001_2008-09-14
skip download for 38 on 2008
Archive already extracted : ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D038_2008-09-14
work on ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D038_2008-09-14
Go to to https://data.geopf.fr/telechargement/download/BDTOPO/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14.7z
../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14.7z downloaded !
extration process... ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14.7z
extracted ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14
work on ../data/raw/BDTOPO/2008/BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D069_2008-09-14
-- Process buildings and communes --


/tmp/ipykernel_41809/785768148.py:46: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  bati.to_file(os.path.join(out_dir_processed, f"bati_indus_{name_roi}_{year}.shp"))


year 2008 done
==== 2013 ====
Go to to https://data.geopf.fr/telechargement/download/BDTOPO/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10.7z
../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10.7z downloaded !
extration process... ../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10.7z
extracted ../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10
work on ../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D001_2013-04-10
Go to to https://data.geopf.fr/telechargement/download/BDTOPO/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D038_2013-04-10/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D038_2013-04-10.7z
../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D038_2013-04-10.7z downloaded !
extration process... ../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D038_2013-04-10.7z
extracted ../data/raw/BDTOPO/2013/BDTOPO_2-1_TOUSTHEMES_SHP_LAMB93_D038_2013-04-10
work on ../data/raw/BDTOP

/tmp/ipykernel_41809/785768148.py:46: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  bati.to_file(os.path.join(out_dir_processed, f"bati_indus_{name_roi}_{year}.shp"))


year 2013 done
==== 2023 ====
Go to to https://data.geopf.fr/telechargement/download/BDTOPO/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15.7z
../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15.7z downloaded !
extration process... ../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15.7z
extracted ../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15
work on ../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D001_2023-03-15
Go to to https://data.geopf.fr/telechargement/download/BDTOPO/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-03-15/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-03-15.7z
../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-03-15.7z downloaded !
extration process... ../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-03-15.7z
extracted ../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-03-15
work on ../data/raw/BDTOP

/tmp/ipykernel_41809/785768148.py:46: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  bati.to_file(os.path.join(out_dir_processed, f"bati_indus_{name_roi}_{year}.shp"))


year 2023 done


# Annexes

In [20]:
bati_2023 = gpd.read_file("/home/rustt/Documents/IGAST/2_PROJETS/Projet_analyse_spatiale/data/processed/BDTOPO/2023/bati_lyon_2023.shp")

In [21]:
bati_2023.shape

(15837, 54)

In [34]:
test_dir = os.path.join(y_dir, "BDTOPO_2-0_TOUSTHEMES_SHP_LAMB93_D001_2008-09-14")

In [373]:
path = "/home/rustt/Documents/IGAST/2_PROJETS/Projet_analyse_spatiale/data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-12-15"
#df = gpd.read_file(path)

In [376]:
extract_communes_path(path, ext=".shp")

None


In [377]:
target_dir_path = None
for r, dirs, files in os.walk(path): 
    if any([_ for _ in files if _ == "COMMUNE.{shp}"]):
        target_dir_path = os.path.join(r, "COMMUNE.shp")
        break

In [378]:
target_dir_path

'/home/rustt/Documents/IGAST/2_PROJETS/Projet_analyse_spatiale/data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D038_2023-12-15/BDTOPO/1_DONNEES_LIVRAISON_2023-12-00099/BDT_3-3_SHP_LAMB93_D038-ED2023-12-15/ADMINISTRATIF/COMMUNE.shp'

In [345]:
extract_communes_path(path)

In [ ]:
path = os.path.join("../data", "processed", "BDTOPO", "2008", "communes_2008.shp")
df = gpd.read_file(path, crs=CRS)

In [ ]:
path = os.path.join("../data", "processed", "BDTOPO", "2013", "communes_2013.shp")
df = gpd.read_file(path, crs=CRS)

In [ ]:
path = os.path.join("../data", "processed", "BDTOPO", "2013", "communes_2013.shp")
df = gpd.read_file(path, crs=CRS)

In [ ]:
df.explore()

### 2023

In [11]:
bati_path_2023 = "/home/rustt/Documents/IGAST/2_PROJETS/Projet_analyse_spatiale/data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D069_2023-12-15/BDTOPO/1_DONNEES_LIVRAISON_2023-12-00099/BDT_3-3_SHP_LAMB93_D069-ED2023-12-15/BATI/BATIMENT.shp"

In [12]:
bati = gpd.read_file(bati_path_2023)

In [13]:
bati.shape

(898689, 28)

In [14]:
bati.columns

Index(['ID', 'NATURE', 'USAGE1', 'USAGE2', 'LEGER', 'ETAT', 'DATE_CREAT',
       'DATE_MAJ', 'DATE_APP', 'DATE_CONF', 'SOURCE', 'ID_SOURCE',
       'ACQU_PLANI', 'PREC_PLANI', 'ACQU_ALTI', 'PREC_ALTI', 'NB_LOGTS',
       'NB_ETAGES', 'MAT_MURS', 'MAT_TOITS', 'HAUTEUR', 'Z_MIN_SOL',
       'Z_MIN_TOIT', 'Z_MAX_TOIT', 'Z_MAX_SOL', 'ORIGIN_BAT', 'APP_FF',
       'geometry'],
      dtype='object')

In [15]:
bati.head()

ID          NATURE         USAGE1 USAGE2 LEGER  \
0  BATIMENT0000000008928193  Indifférenciée  Indifférencié    NaN   Non   
1  BATIMENT0000002244089604  Indifférenciée  Indifférencié    NaN   Non   
2  BATIMENT0000000258845240  Indifférenciée  Indifférencié    NaN   Non   
3  BATIMENT0000000258521822  Indifférenciée  Indifférencié    NaN   Non   
4  BATIMENT0000000258846024  Indifférenciée    Résidentiel    NaN   Non   

         ETAT           DATE_CREAT             DATE_MAJ    DATE_APP DATE_CONF  \
0  En service  2006-07-31 14:13:55  2021-05-25 17:36:41         NaN       NaN   
1  En service  2021-05-26 11:38:12  2023-04-19 13:52:29         NaN       NaN   
2  En service  2011-05-31 10:45:47  2021-05-26 11:40:14         NaN       NaN   
3  En service  2011-05-24 16:40:49  2021-05-26 11:45:02         NaN       NaN   
4  En service  2011-05-31 10:51:27  2023-04-19 14:16:54  1790-01-01       NaN   

   ... MAT_MURS MAT_TOITS HAUTEUR  Z_MIN_SOL Z_MIN_TOIT  Z_MAX_TOIT  \
0  ...      NaN       NaN     3.8      193.0        NaN       197.6   
1  ...      NaN       NaN     5.3      229.3      234.7       237.6   
2  ...      NaN       NaN     6.5      199.4      205.9       206.9   
3  ...      NaN       NaN    13.6      203.0      216.6       220.0   
4  ...       90        10     4.1      191.5      195.6       198.2   

   Z_MAX_SOL         ORIGIN_BAT APP_FF  \
0      194.0  Imagerie aérienne    NaN   
1      230.0           Cadastre    NaN   
2      200.5           Cadastre    NaN   
3      205.8           Cadastre    NaN   
4      191.6           Cadastre  C 0.4   

                                            geometry  
0  POLYGON Z ((859536.400 6528576.900 196.700, 85...  
1  POLYGON Z ((840078.500 6543439.500 234.700, 84...  
2  POLYGON Z ((840672.100 6564601.900 205.900, 84...  
3  POLYGON Z ((859492.000 6530398.100 216.600, 85...  
4  POLYGON Z ((843123.500 6563798.000 195.600, 84...  

[5 rows x 28 columns]

In [21]:
bati.NATURE.value_counts()

NATURE
Indifférenciée                        837486
Industriel, agricole ou commercial     55227
Serre                                   3570
Eglise                                   947
Château                                  733
Tour, donjon                             223
Chapelle                                 204
Silo                                     142
Tribune                                  117
Fort, blockhaus, casemate                 21
Arène ou théâtre antique                  11
Monument                                   7
Moulin à vent                              1
Name: count, dtype: int64

In [24]:
bati[bati.NATURE == "Industriel, agricole ou commercial"]["USAGE1"].value_counts()

USAGE1
Indifférencié             21548
Industriel                12577
Agricole                   8614
Commercial et services     7612
Annexe                     3173
Résidentiel                1687
Sportif                      16
Name: count, dtype: int64

In [28]:
bati[bati.NATURE == "Commercial et services"]["USAGE1"].value_counts()

Series([], Name: count, dtype: int64)

In [17]:
bati.USAGE1.value_counts(dropna=False)

USAGE1
Indifférencié             403875
Résidentiel               364493
Annexe                     69297
Commercial et services     33020
Industriel                 13031
Agricole                   12333
Sportif                     1403
Religieux                   1237
Name: count, dtype: int64

In [18]:
bati.USAGE2.value_counts(dropna=False)

USAGE2
NaN                       802885
Annexe                     66970
Commercial et services     19775
Résidentiel                 8867
Industriel                   180
Indifférencié                 10
Sportif                        2
Name: count, dtype: int64

In [29]:
bati[bati.USAGE2 == "Industriel"]['NATURE'].value_counts()

NATURE
Industriel, agricole ou commercial    107
Indifférenciée                         72
Silo                                    1
Name: count, dtype: int64

In [33]:
bati[(bati.NATURE == "Industriel, agricole ou commercial") & (bati.USAGE2 == "Industriel")]["USAGE1"].value_counts()

USAGE1
Commercial et services    81
Agricole                  24
Résidentiel                2
Name: count, dtype: int64

### Join on cunary_union

In [10]:
com = gpd.read_file("../data/raw/BDTOPO/2023/BDTOPO_3-3_TOUSTHEMES_SHP_LAMB93_D069_2023-03-15/BDTOPO/1_DONNEES_LIVRAISON_2023-03-00212/BDT_3-3_SHP_LAMB93_D069-ED2023-03-15/ADMINISTRATIF/COMMUNE.shp")

In [19]:
roi_buffer = gpd.GeoSeries(Point(centroid_lyon), crs=CRS).buffer(DIST_RADIUS).to_frame()

In [20]:
roi_buffer.explore()

In [24]:
gpd.sjoin(com, roi_buffer, how="inner", predicate="intersects").explore()

In [25]:
rio_com_union = gpd.sjoin(com, roi_buffer, how="inner", predicate="intersects").dissolve()

In [26]:
rio_com_union.explore()